**PREDCTION OF FUTURE STOCK PRICES**

#TASK #2

In [ ]:
#Importing libraries

import pandas as pd
import plotly.express as px
from copy import copy
from scipy import stats
import matplotlib.pyplot as plt
import numpy as np
import plotly.figure_factory as ff
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from tensorflow import keras

In [ ]:
#Mounting Drive

from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
#Importing Dataset

data_stock = pd.read_csv("/content/drive/MyDrive/stock.csv")
data_stockvol = pd.read_csv("/content/drive/MyDrive/stock_volume.csv")

In [ ]:
#Reading Stock Price Data

print(data_stock)

            Date        AAPL          BA          T        MGM         AMZN  \
0     2012-01-12   60.198570   75.510002  30.120001  12.130000   175.929993   
1     2012-01-13   59.972858   74.599998  30.070000  12.350000   178.419998   
2     2012-01-17   60.671429   75.239998  30.250000  12.250000   181.660004   
3     2012-01-18   61.301430   75.059998  30.330000  12.730000   189.440002   
4     2012-01-19   61.107143   75.559998  30.420000  12.800000   194.449997   
...          ...         ...         ...        ...        ...          ...   
2154  2020-08-05  440.250000  174.279999  29.850000  16.719999  3205.030029   
2155  2020-08-06  455.609985  172.199997  29.840000  18.459999  3225.000000   
2156  2020-08-07  444.450012  170.020004  30.020000  19.030001  3167.459961   
2157  2020-08-10  450.910004  179.410004  30.200001  21.650000  3148.159912   
2158  2020-08-11  437.500000  180.130005  30.200001  21.500000  3080.669922   

             IBM         TSLA         GOOG        s

In [ ]:
#Reading Stock Volume Data

print(data_stockvol)

            Date      AAPL        BA         T       MGM     AMZN      IBM  \
0     2012-01-12  53146800   3934500  26511100  17891100  5385800  6881000   
1     2012-01-13  56505400   4641100  22096800  16621800  4753500  5279200   
2     2012-01-17  60724300   3700100  23500200  15480800  5644500  6003400   
3     2012-01-18  69197800   4189500  22015000  18387600  7473500  4600600   
4     2012-01-19  65434600   5397300  25524000  14022900  7096000  8567200   
...          ...       ...       ...       ...       ...      ...      ...   
2154  2020-08-05  30498000  46551000  22991700  18914200  3930000  3675400   
2155  2020-08-06  50607200  32921600  21908700  35867700  3940600  3417100   
2156  2020-08-07  49453300  19301600  30398500  34530300  3929600  3651000   
2157  2020-08-10  53100900  35857700  35514400  71219700  3167300  3968300   
2158  2020-08-11  46871100  60966900  30978300  34357900  3706600  4998500   

         TSLA      GOOG       sp500  
0      729300   3764400  

In [ ]:
#Sorting Price and Volume Data as per 'Date'

data_stock.sort_values("Date",inplace=True)
data_stockvol.sort_values("Date",inplace=True)

In [ ]:
#Checking if Null values exist in price and volume data 

data_stock.isnull().sum()

Date     0
AAPL     0
BA       0
T        0
MGM      0
AMZN     0
IBM      0
TSLA     0
GOOG     0
sp500    0
dtype: int64

In [ ]:
data_stockvol.isnull().sum()

Date     0
AAPL     0
BA       0
T        0
MGM      0
AMZN     0
IBM      0
TSLA     0
GOOG     0
sp500    0
dtype: int64

In [ ]:
#Stock Price and Volume Dataframe and Info

df_stock = pd.DataFrame(data_stock)
df_stock.describe()

AAPL           BA            T          MGM         AMZN  \
count  2159.000000  2159.000000  2159.000000  2159.000000  2159.000000   
mean    140.819823   189.942700    35.162899    23.105743   915.665665   
std      70.827601   103.678586     3.207490     6.963847   697.838905   
min      55.790001    67.239998    26.770000     7.140000   175.929993   
25%      89.165714   124.015000    33.040001    18.545000   316.490005   
50%     116.599998   142.419998    34.930000    23.780001   676.010010   
75%     175.019997   297.044998    37.419998    28.430000  1593.645019   
max     455.609985   440.619995    43.470001    38.029999  3225.000000   

               IBM         TSLA         GOOG        sp500  
count  2159.000000  2159.000000  2159.000000  2159.000000  
mean    161.853001   259.600815   783.712512  2218.749554  
std      25.561938   210.988003   334.448057   537.321727  
min      94.769997    22.790001   278.481171  1278.040039  
25%     142.769997   184.595001   527.214416  1847.984985  
50%     156.949997   231.960007   737.599976  2106.629883  
75%     185.974998   307.350006  1079.744995  2705.810059  
max     215.800003  1643.000000  1568.489990  3386.149902

In [ ]:
df_stockvol = pd.DataFrame(data_stockvol)
df_stockvol.describe()

AAPL            BA             T           MGM          AMZN  \
count  2.159000e+03  2.159000e+03  2.159000e+03  2.159000e+03  2.159000e+03   
mean   5.820332e+07  6.419916e+06  2.832131e+07  9.845582e+06  4.102673e+06   
std    4.568141e+07  9.711873e+06  1.428911e+07  7.295753e+06  2.290722e+06   
min    1.136200e+07  7.889000e+05  6.862400e+06  9.507000e+05  8.813000e+05   
25%    2.769930e+07  3.031850e+06  2.002150e+07  5.796450e+06  2.675700e+06   
50%    4.209420e+07  3.991000e+06  2.485930e+07  7.899800e+06  3.494800e+06   
75%    7.182480e+07  5.325900e+06  3.210565e+07  1.104055e+07  4.768150e+06   
max    3.765300e+08  1.032128e+08  1.950827e+08  9.009820e+07  2.385610e+07   

                IBM          TSLA          GOOG         sp500  
count  2.159000e+03  2.159000e+03  2.159000e+03  2.159000e+03  
mean   4.453090e+06  7.001302e+06  2.498238e+06  3.680732e+09  
std    2.462811e+06  5.781208e+06  1.928407e+06  8.622717e+08  
min    1.193000e+06  3.649000e+05  7.900000e+03  1.248960e+09  
25%    3.111250e+06  3.433450e+06  1.325400e+06  3.211890e+09  
50%    3.825000e+06  5.581100e+06  1.813900e+06  3.526890e+09  
75%    4.937300e+06  8.619550e+06  3.245350e+06  3.933290e+09  
max    3.049020e+07  6.093880e+07  2.497790e+07  9.044690e+09

#TASK #3 - Performing exploratory data analysis and visualization

In [ ]:
#Normalizing Function

def normalize(df):
    x = df.copy()
    for j in x.columns[1:]:
        x[j] = x[j]/x[j][0]
    return x

In [ ]:
df_stock_normalized = normalize(df_stock)
df_stockvol_normalized= normalize(df_stockvol)

In [ ]:
#Function to plot interactive plot

def interactive_plot(df, title):
    fig = px.line (title = title)

    for i in df.columns[1:]:
        fig.add_scatter(x = df['Date'], y = df[i], name = i)
    
    fig.show()

In [ ]:
interactive_plot(df_stock,'Interactive Plot of the Price Data')

In [ ]:
interactive_plot(df_stockvol,'Interactive Plot of the Volume Data')

#Task #4 - Preparing the data before training the AI/ML Model

In [ ]:
#Function to concatente

def individual_stock(pricedf, voldf, nameofstock):
    return pd.DataFrame({'Date': pricedf['Date'], 'Close': pricedf[nameofstock], 'Volume': voldf[nameofstock]})

In [ ]:
#Function to return input/output data for AI/ML Model

def trading_window(data):
  
  n = 1
  data['Target'] = data[['Close']].shift(-n)
  return data

In [ ]:
#Checking functionality of functions for Apple Stock

pricevolume_df = individual_stock(df_stock, df_stockvol, 'AAPL')
pricevolume_df

Date       Close    Volume
0     2012-01-12   60.198570  53146800
1     2012-01-13   59.972858  56505400
2     2012-01-17   60.671429  60724300
3     2012-01-18   61.301430  69197800
4     2012-01-19   61.107143  65434600
...          ...         ...       ...
2154  2020-08-05  440.250000  30498000
2155  2020-08-06  455.609985  50607200
2156  2020-08-07  444.450012  49453300
2157  2020-08-10  450.910004  53100900
2158  2020-08-11  437.500000  46871100

[2159 rows x 3 columns]

In [ ]:
pricevolumetarget_df = trading_window(pricevolume_df)
pricevolumetarget_df

Date       Close    Volume      Target
0     2012-01-12   60.198570  53146800   59.972858
1     2012-01-13   59.972858  56505400   60.671429
2     2012-01-17   60.671429  60724300   61.301430
3     2012-01-18   61.301430  69197800   61.107143
4     2012-01-19   61.107143  65434600   60.042858
...          ...         ...       ...         ...
2154  2020-08-05  440.250000  30498000  455.609985
2155  2020-08-06  455.609985  50607200  444.450012
2156  2020-08-07  444.450012  49453300  450.910004
2157  2020-08-10  450.910004  53100900  437.500000
2158  2020-08-11  437.500000  46871100         NaN

[2159 rows x 4 columns]

In [ ]:
# Removing the last row as it will be a null value

pricevolumetarget_df = pricevolumetarget_df[:-1]
pricevolumetarget_df

Date       Close    Volume      Target
0     2012-01-12   60.198570  53146800   59.972858
1     2012-01-13   59.972858  56505400   60.671429
2     2012-01-17   60.671429  60724300   61.301430
3     2012-01-18   61.301430  69197800   61.107143
4     2012-01-19   61.107143  65434600   60.042858
...          ...         ...       ...         ...
2153  2020-08-04  438.660004  43267900  440.250000
2154  2020-08-05  440.250000  30498000  455.609985
2155  2020-08-06  455.609985  50607200  444.450012
2156  2020-08-07  444.450012  49453300  450.910004
2157  2020-08-10  450.910004  53100900  437.500000

[2158 rows x 4 columns]

In [ ]:
# Scaling the data

from sklearn.preprocessing import MinMaxScaler
sc = MinMaxScaler(feature_range = (0, 1))
pricevolumetargetscaled_df = sc.fit_transform(pricevolumetarget_df.drop(columns = ['Date']))

In [ ]:
# Creating Feature and Target

X = pricevolumetargetscaled_df[:,:2]
y = pricevolumetargetscaled_df[:,2:]

In [ ]:
# Spliting the data this way, since order is important in time-series
# Note that we did not use train test split with it's default settings since it shuffles the data

split = int(0.65 * len(X))
X_train = X[:split]
y_train = y[:split]
X_test = X[split:]
y_test = y[split:]

In [ ]:
# Defining a data plotting function

def show_plot(data, title):
  plt.figure(figsize = (13, 5))
  plt.plot(data, linewidth = 3)
  plt.title(title)
  plt.grid()

#TASK #7 - BUILD AND TRAIN A RIDGE LINEAR REGRESSION MODEL

In [ ]:
from sklearn.linear_model import Ridge
regression_model = Ridge()
regression_model.fit(X_train, y_train)

Ridge()

In [ ]:
# Testing the model and its accuracy 

lraccuracy = regression_model.score(X_test, y_test)
print("Linear Regression Score: ", lraccuracy)

Linear Regression Score:  0.7950028030821767


In [ ]:
# Making Prediction

predictedprices = regression_model.predict(X)
predictedprices

array([[0.03466412],
       [0.03374627],
       [0.03451936],
       ...,
       [0.81048342],
       [0.78876033],
       [0.80091324]])

In [ ]:
# Appending the predicted values into a list

Predicted = []
for i in predictedprices:
  Predicted.append(i[0])

In [ ]:
# Append the close values to the list

close = []
for i in pricevolumetargetscaled_df:
  close.append(i[0])

In [ ]:
# Create a dataframe based on the dates in the individual stock data

df_predicted = pricevolumetarget_df[['Date']]
df_predicted

Date
0     2012-01-12
1     2012-01-13
2     2012-01-17
3     2012-01-18
4     2012-01-19
...          ...
2153  2020-08-04
2154  2020-08-05
2155  2020-08-06
2156  2020-08-07
2157  2020-08-10

[2158 rows x 1 columns]

In [ ]:
# Adding the close values to the dataframe

df_predicted['Close'] = close
df_predicted

Date     Close
0     2012-01-12  0.011026
1     2012-01-13  0.010462
2     2012-01-17  0.012209
3     2012-01-18  0.013785
4     2012-01-19  0.013299
...          ...       ...
2153  2020-08-04  0.957606
2154  2020-08-05  0.961583
2155  2020-08-06  1.000000
2156  2020-08-07  0.972088
2157  2020-08-10  0.988245

[2158 rows x 2 columns]

In [ ]:
# Adding the predicted values to the dataframe

df_predicted['Prediction'] = Predicted
df_predicted

Date     Close  Prediction
0     2012-01-12  0.011026    0.034664
1     2012-01-13  0.010462    0.033746
2     2012-01-17  0.012209    0.034519
3     2012-01-18  0.013785    0.034556
4     2012-01-19  0.013299    0.034707
...          ...       ...         ...
2153  2020-08-04  0.957606    0.778280
2154  2020-08-05  0.961583    0.783205
2155  2020-08-06  1.000000    0.810483
2156  2020-08-07  0.972088    0.788760
2157  2020-08-10  0.988245    0.800913

[2158 rows x 3 columns]

In [ ]:
# Plotting the results

interactive_plot(df_predicted, "Original Vs. Predicted")

#TASK #12 - TRAINING AN LSTM MODEL

In [ ]:
# Let's test the functions and get individual stock prices and volumes for Apple Stock

pricevolumedfpricevolume_df = individual_stock(df_stock, df_stockvol, 'AAPL')
pricevolume_df

Date       Close    Volume      Target
0     2012-01-12   60.198570  53146800   59.972858
1     2012-01-13   59.972858  56505400   60.671429
2     2012-01-17   60.671429  60724300   61.301430
3     2012-01-18   61.301430  69197800   61.107143
4     2012-01-19   61.107143  65434600   60.042858
...          ...         ...       ...         ...
2154  2020-08-05  440.250000  30498000  455.609985
2155  2020-08-06  455.609985  50607200  444.450012
2156  2020-08-07  444.450012  49453300  450.910004
2157  2020-08-10  450.910004  53100900  437.500000
2158  2020-08-11  437.500000  46871100         NaN

[2159 rows x 4 columns]

In [ ]:
# Get the close and volume data as training data (Input)

trainingdata = pricevolume_df.iloc[:, 1:3].values
trainingdata

array([[6.01985700e+01, 5.31468000e+07],
       [5.99728580e+01, 5.65054000e+07],
       [6.06714290e+01, 6.07243000e+07],
       ...,
       [4.44450012e+02, 4.94533000e+07],
       [4.50910004e+02, 5.31009000e+07],
       [4.37500000e+02, 4.68711000e+07]])

In [ ]:
# Normalizing the data

from sklearn.preprocessing import MinMaxScaler
sc = MinMaxScaler(feature_range = (0, 1))
trainingset_scaled = sc.fit_transform(trainingdata)

In [ ]:
# Creating the training and testing data, training data contains present day and previous day values

X = []
y = []
for i in range(1, len(pricevolume_df)):
    X.append(trainingset_scaled [i-1:i, 0])
    y.append(trainingset_scaled [i, 0])

In [ ]:
# Converting the data to arrays

X = np.asarray(X)
y = np.asarray(y)

In [ ]:
# Spliting the data

split = int(0.7 * len(X))
X_train = X[:split]
y_train = y[:split]
X_test = X[split:]
y_test = y[split:]

In [ ]:
# Reshaping the 1D arrays to 3D arrays to feed in the model

X_train = np.reshape(X_train, (X_train.shape[0], X_train.shape[1], 1))
X_test = np.reshape(X_test, (X_test.shape[0], X_test.shape[1], 1))
X_train.shape, X_test.shape

((1510, 1, 1), (648, 1, 1))

In [ ]:
# Creating the model

inputs = keras.layers.Input(shape=(X_train.shape[1], X_train.shape[2]))
x = keras.layers.LSTM(150, return_sequences= True)(inputs)
x = keras.layers.Dropout(0.3)(x)
x = keras.layers.LSTM(150, return_sequences=True)(x)
x = keras.layers.Dropout(0.3)(x)
x = keras.layers.LSTM(150)(x)
outputs = keras.layers.Dense(1, activation='linear')(x)

model = keras.Model(inputs=inputs, outputs=outputs)
model.compile(optimizer='adam', loss="mse")
model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1, 1)]            0         
                                                                 
 lstm (LSTM)                 (None, 1, 150)            91200     
                                                                 
 dropout (Dropout)           (None, 1, 150)            0         
                                                                 
 lstm_1 (LSTM)               (None, 1, 150)            180600    
                                                                 
 dropout_1 (Dropout)         (None, 1, 150)            0         
                                                                 
 lstm_2 (LSTM)               (None, 150)               180600    
                                                                 
 dense (Dense)               (None, 1)                 151   

In [ ]:
# Training the model
history = model.fit(
    X_train, y_train,
    epochs = 20,
    batch_size = 32,
    validation_split = 0.2)

Epoch 1/20
38/38 [==============================] - 8s 50ms/step - loss: 0.0037 - val_loss: 0.0200
Epoch 2/20
38/38 [==============================] - 0s 12ms/step - loss: 0.0018 - val_loss: 0.0040
Epoch 3/20
38/38 [==============================] - 0s 11ms/step - loss: 1.9227e-04 - val_loss: 3.1826e-05
Epoch 4/20
38/38 [==============================] - 0s 12ms/step - loss: 5.6435e-05 - val_loss: 1.6315e-05
Epoch 5/20
38/38 [==============================] - 0s 12ms/step - loss: 4.3568e-05 - val_loss: 1.6547e-05
Epoch 6/20
38/38 [==============================] - 1s 15ms/step - loss: 3.8833e-05 - val_loss: 1.6394e-05
Epoch 7/20
38/38 [==============================] - 1s 13ms/step - loss: 4.1148e-05 - val_loss: 2.1025e-05
Epoch 8/20
38/38 [==============================] - 0s 12ms/step - loss: 3.6619e-05 - val_loss: 3.1655e-05
Epoch 9/20
38/38 [==============================] - 0s 12ms/step - loss: 3.7008e-05 - val_loss: 2.1228e-05
Epoch 10/20
38/38 [==============================] - 

In [ ]:
# Making prediction

predicted = model.predict(X)
predicted

array([[0.01528428],
       [0.01473323],
       [0.01643875],
       ...,
       [0.95826983],
       [0.9335811 ],
       [0.9478939 ]], dtype=float32)

***END OF PROJECT WORK***